In [74]:
import folium
import geopandas as gpd
import numpy as np
import osmnx as ox
import pandas as pd
from shapely.geometry import Point


def charger_les_colleges(f = "./fr-en-adresse-et-geolocalisation-etablissements-premier-et-second-degre.csv"):
    colleges= pd.read_csv(f, sep=";")
    def create_geometry(row):
          row["geometry"] = Point(row[0],row[1])
          return row
    positions = colleges["Position"].str.split(",", expand=True).astype(np.float64).apply(create_geometry, axis=1)
    colleges["geometry"] = positions["geometry"]
    geo_colleges = gpd.GeoDataFrame(colleges)
    return geo_colleges
    
def get_point(location_str): 
    import shapely
    df = gpd.tools.geocode(  
            [location_str]
        )
    # print(df.crs)
    thorigne = [df["geometry"].iloc[0].y, df["geometry"].iloc[0].x]
    thorigne_point = shapely.Point(*thorigne)
    return thorigne_point

# on ne garde que quelques colleges proches dans la bbox
def colleges_proches(geo_colleges, bbox):
    print(f"colleges_proches bbox = {bbox}")
    geo_colleges_proches = geo_colleges[geo_colleges.within(bbox)]
    return geo_colleges_proches
    

def get_nodes(Gp, geo_colleges, origin):
    uid = ox.nearest_nodes(Gp, origin.y, origin.x)
    origin_node = dict(uid=uid, **Gp.nodes(data=True)[uid])

    college_nodes = []
    for _, row in geo_colleges.iterrows():
        print(row["Appellation officielle"])
        c = row.geometry
        uid = ox.nearest_nodes(Gp, c.y, c.x)
        node = Gp.nodes(data=True)[uid]
        college_nodes.append(dict(row=row, uid=uid, **node))
        # vérification que le noeud qu'on trouve est vraiment proche de ce qu'on cherche
        #print(row)
    return Gp, origin_node, college_nodes

def draw(Gp, origin_node, college_nodes):
    map = folium.Map(location=[origin_node["y"], origin_node["x"]], tiles="OpenStreetMap", zoom_start=10)
    map.add_child(folium.Marker(location=[origin_node["y"], origin_node["x"]], icon=folium.Icon(icon="home")))
        
    for college_node in college_nodes:
        row = college_node["row"]
        nom_college = row["Appellation officielle"]
        route = ox.shortest_path(Gp, origin_node["uid"], college_node["uid"], weight="length")
        if route is None:
            continue
        length = int(sum(ox.utils_graph.get_route_edge_attributes(Gp, route, "length")))

        print(f"{nom_college} -> {length}m")
        map = ox.plot_route_folium(Gp, route, route_map=map, color="red")
        color = "blue" if row["Secteur Public/Privé"] == "Public" else "purple" 
        map.add_child(folium.Marker(location=[college_node["y"], college_node["x"]],
                                    popup=folium.Popup(f"<div>{nom_college} <br/>Distance = {length/1000}km</div>", max_width="200"),
                                    icon=folium.Icon(color=color)))
        
    return map  


def draw_closest_colleges(location, dist=4000):
    origin_point = get_point(location)

    (latmax, latmin, lonmax, lonmin) = ox.utils_geo.bbox_from_point([origin_point.x, origin_point.y], dist=dist)
    osmx_bbox = ox.utils_geo.bbox_to_poly(latmax, latmin, lonmax, lonmin)
    
    G = ox.graph_from_polygon(osmx_bbox, network_type="drive")
    Gp = ox.project_graph(G, to_crs="EPSG:4326")
    # ox.plot_graph(Gp)
    Gp = ox.add_edge_speeds(Gp, fallback=12)
    # calculate travel time (seconds) for all edges
    edges = ox.graph_to_gdfs(Gp, nodes=False)
    
    import shapely
    geo_colleges_proches = colleges_proches(geo_colleges, shapely.box(latmin, lonmin, latmax, lonmax))
    return (draw(*get_nodes(Gp, geo_colleges_proches, origin_point))),geo_colleges_proches

# Quelques communes

In [75]:
map, colleges = draw_closest_colleges("Thorigné-Fouillard ille-et-vilaine, France", dist=7000)
map

colleges_proches bbox = POLYGON ((48.21647572348451 -1.674385868486704, 48.21647572348451 -1.485661731513296, 48.0905708765155 -1.485661731513296, 48.0905708765155 -1.674385868486704, 48.21647572348451 -1.674385868486704))
Collège privé Saint Michel
Collège Clotilde Vautier
Collège Bourgchevreuil
Collège privé Léontine-Dolivet
Collège privé hors-contrat Notre-Dame Auxiliatrice
Collège Martin Luther King
Collège Jacques Brel
Collège François Truffaut
Collège Les Gayeulles
Collège Les Ormeaux
Collège privé Saint Hélier
Collège Le Landry
Collège privé Joséphine-Bakhita
Ecole privée hors contrat HOLISKOL
Collège Anne de Bretagne
Collège Emile Zola
Collège privé Saint Vincent-Providence
Collège privé Assomption
Collège privé Saint-Louis
Collège privé Saint Michel -> 9160m
Collège Clotilde Vautier -> 8035m
Collège Bourgchevreuil -> 5126m
Collège privé Léontine-Dolivet -> 3758m
Collège privé hors-contrat Notre-Dame Auxiliatrice -> 6731m
Collège Martin Luther King -> 9655m
Collège Jacques Brel

In [76]:
map, colleges = draw_closest_colleges("Chantepie ille-et-vilaine, France", dist=7000)
map

colleges_proches bbox = POLYGON ((48.151107423484504 -1.7113902713762958, 48.151107423484504 -1.522906128623704, 48.0252025765155 -1.522906128623704, 48.0252025765155 -1.7113902713762958, 48.151107423484504 -1.7113902713762958))
Collège Echange
Collège Clotilde Vautier
Collège Bourgchevreuil
Collège privé Léontine-Dolivet
Collège Les Chalais
Collège Jacques Brel
Collège Les Gayeulles
Collège Les Ormeaux
Collège privé Notre-Dame du Vieux Cours
Collège privé Saint Hélier
Collège des Hautes Ourmes
Collège Le Landry
Collège privé Joséphine-Bakhita
Ecole privée hors contrat HOLISKOL
Collège Cleunay
Collège privé Saint-Martin quartier Sainte Geneviève
Collège La Binquenais
Collège de Fontenay
Collège Théodore Monod
Collège privé La Tour d'Auvergne La Salle
Collège Anne de Bretagne
Collège Emile Zola
Collège privé Saint Vincent-Providence
Collège privé Assomption
Collège privé Saint-Louis
Collège Echange -> 6964m
Collège Clotilde Vautier -> 6291m
Collège Bourgchevreuil -> 4870m
Collège privé 

In [77]:
map, colleges = draw_closest_colleges("Saint-Grégoire ille-et-vilaine, France", dist=7000)
map

colleges_proches bbox = POLYGON ((48.215365323484505 -1.7797580265393895, 48.215365323484505 -1.5910379734606104, 48.0894604765155 -1.5910379734606104, 48.0894604765155 -1.7797580265393895, 48.215365323484505 -1.7797580265393895))
Collège Echange
Collège Clotilde Vautier
Collège Bourgchevreuil
Collège Françoise Dolto
Collège privé Saint Gabriel
Collège privé Léontine-Dolivet
Collège privé hors-contrat Notre-Dame Auxiliatrice
Collège François Truffaut
Collège Les Gayeulles
Collège Les Ormeaux
Collège privé Notre-Dame du Vieux Cours
Collège privé Saint Hélier
Collège des Hautes Ourmes
Collège Le Landry
Collège privé Joséphine-Bakhita
Collège privé HC Ste-Philomène
Ecole privée hors contrat HOLISKOL
Collège Cleunay
Collège privé Immaculée
Collège privé Saint-Martin quartier Sainte Geneviève
Collège Rosa Parks
Collège La Binquenais
Collège Germaine Tillion
Collège privé HC Montessori Workshop St-Grégoire
Collège privé La Tour d'Auvergne La Salle
Collège Anne de Bretagne
Collège Emile Zola
